# Install Necessary packages


In [1]:
!pip install transformers datasets sentence_transformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.7/7.7 MB 57.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 519.6/519.6 kB 52.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.0/86.0 kB 12.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.0/302.0 kB 36.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 100.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 86.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 16.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 19.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 79.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 295.0/295.0 kB 30.9 MB/s eta 0:00:00
  Created wheel for sentence_transformers: filename=sentence_transformers-2.2.2-py3-none-any.whl size=125923 sha256=b5056d949370399efecafac47bbdd0

# Importing Libraries

In [2]:
import pandas as pd

import torch

from datasets import load_dataset

from sentence_transformers import SentenceTransformer, util

## Instantiate Dataset and model

In [3]:
dataset_name = "multi_news"
embedding_model = "TaylorAI/gte-tiny"

## Load Dataset

In [4]:
dataset = load_dataset(dataset_name, split='test')
df = dataset.to_pandas().sample(2000, random_state=42)

Generating train split:   0%|          | 0/44972 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/5622 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/5622 [00:00<?, ? examples/s]

In [5]:
df.head()

document  \
4830  Tweet with a location \n \n You can add locati...   
1255  CNN host Piers Morgan just called to discuss h...   
80    White House communications director Anthony Sc...   
3044  CLOSE Scientists say they've found archaeologi...   
4486  Click image above to view graphic \n \n Althou...   

                                                summary  
4830  – Denis Finley has taken to Twitter to call Po...  
1255  – CNN's Piers Morgan thinks gun-rights propone...  
80    – New White House communications director Anth...  
3044  – Scientists say they have the first physical ...  
4486  – Scientists are calling it a breakthrough and...

### Sentence transformer

In [6]:
model = SentenceTransformer(embedding_model)

In [7]:
model

SentenceTransformer(
  (0): Transformer({'max_seq_length': 512, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False})
)

In [8]:
passage_embeddings = list(
      model.encode(df['summary'].to_list(),
      show_progress_bar=True
    ))

Batches:   0%|          | 0/63 [00:00<?, ?it/s]

In [9]:
passage_embeddings

[array([-6.13048263e-02,  2.88158566e-01,  4.65740561e-02, -1.42064452e-01,
        -2.60759685e-02,  1.21696435e-01,  4.67796504e-01,  4.73569572e-01,
        -1.15705654e-02, -4.95422482e-02,  1.06296979e-01,  7.59340003e-02,
         2.30518907e-01,  1.20788710e-02,  4.96897213e-02,  7.87576437e-02,
         2.38808870e-01, -2.00858653e-01,  3.78855760e-03,  5.39292574e-01,
         2.81184137e-01, -2.91690230e-01,  6.70917109e-02, -4.19459313e-01,
         4.55776423e-01, -1.31807730e-01, -6.03834867e-01, -1.13963172e-01,
        -4.84033823e-01, -1.49689257e+00,  1.38087198e-02, -3.46139699e-01,
         1.54760897e-01, -2.38961652e-01,  7.78024644e-02, -2.88705647e-01,
        -1.43086076e-01,  8.99646655e-02, -9.08318833e-02,  3.75294387e-01,
         4.19759899e-01,  2.19642185e-02, -4.58032966e-01, -4.89734262e-01,
        -1.73244402e-01,  3.69573325e-01, -1.52751654e-01, -1.06785811e-01,
        -2.39626095e-02, -4.13295567e-01,  2.11894475e-02, -5.64086497e-01,
         8.0

In [10]:
len(passage_embeddings)

2000

In [11]:
passage_embeddings[0].shape

(384,)

In [12]:
query = "Find me some articles about technology and Artificial Intelligence"
query_embeddings = model.encode(query)
len(query_embeddings), query_embeddings.shape

(384, (384,))

In [13]:
similarities = util.cos_sim(query_embeddings, passage_embeddings)
similarities.shape

/usr/local/lib/python3.10/dist-packages/sentence_transformers/util.py:39: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at ../torch/csrc/utils/tensor_new.cpp:261.)
  b = torch.tensor(b)


torch.Size([1, 2000])

In [14]:
top_indices = torch.topk(similarities.flatten(), 3).indices
top_indices

tensor([ 206, 1834, 1266])

In [15]:
top_relevant_passages = [df.iloc[x.item()]['summary'][:200] + "....." for x in top_indices]
top_relevant_passages

["– Google has revealed the topic of the year's fastest-rising search request: Robin Williams' suicide. Reaction to his death tops this year's list, the AP reports. Some notable examples: In the first f.....",
 "– Using methods borrowed from Google, a group of researchers has analyzed all Wikipedia pages and determined that, at least on the English language version of the site, Frank Sinatra is the world's mo.....",
 '– Are you a "digital native" or a "digital immigrant," and does it make a difference? Research recently published in the Teaching and Teacher Education journal indicates the concept of so-called digit.....']

## As a function

In [16]:
def find_relevant_news(query):
  query_embeddings = model.encode(query)
  similarities = util.cos_sim(query_embeddings, passage_embeddings)
  top_indices = torch.topk(similarities.flatten(), 3).indices
  top_relevant_passages = [df.iloc[x.item()]['summary'][:200] + "....." for x in top_indices]
  return top_relevant_passages



In [17]:
find_relevant_news("Natural Disasters")

['– A sad milestone out of Japan: Two weeks after the quake struck, its official death toll has broken the 10,000 mark—and that number is still on the rise, with more than 17,400 missing. Police estimat.....',
 '– Like earthquakes can unleash tsunamis, strong winds and the California wildfires apparently set loose another type of natural disaster: fire tornadoes. And the San Francisco Chronicle says the fire-.....',
 '– A massive 7.6 magnitude earthquake struck in the Caribbean Sea Tuesday night—but there were no immediate reports of injuries or major damage after what was one of the strongest earthquakes on record.....']

In [18]:
find_relevant_news("Law enforcement and police")

['– Greg Barnes was in a hurry to get home on Friday, so when he saw police lights behind him on State Road 332 in Muncie, Indiana, "immediately I knew I was in the wrong," he tells WISH. What followed .....',
 "– Not long after 12-year-old Tamir Rice was killed by police in Cleveland in November, a group of students in nearby Akron decided protests weren't enough. So the Akron PeaceMakers, an anti-violence y.....",
 '– "Are you kidding? You\'re about to snort coke on the side of the road?" A routine traffic stop on Tuesday in Seattle ended with one poor police officer getting increasingly incredulous after the 73-y.....']

In [19]:
find_relevant_news("Politics, diplomacy and nationalism")

["– Kim Jong Un is a terrible, murderous despot, but he's not the only Dr. Evil on the block. Ozy runs through some of the equally ruthless dictators who you've likely never heard of: Alexander Lukashen.....",
 '– Members of the low-caste Dalit community in India were once known as "untouchables." How times have changed: Two just competed against each other for the largely ceremonial office of president, and .....',
 '– In his only print interview during a visit to the UN, Mahmoud Ahmadinejad appeared “complex, even bizarre,” writes Nicholas Kristof in the New York Times. The “firebrand” in public was “subdued and .....']